# Pulumiでカスタムモデルをデプロイする

このノートブックでは、Pulumiを使用してScikit-learn分類器をデプロイする方法の概要を説明します。続行する前に、このノートブックでタスクを実行するために[必要なアセットをダウンロード](https://datarobot-doc-assets.s3.us-east-1.amazonaws.com/deploy_custom_model.zip)します。


## 環境の初期化

環境を起動して、DataRobotライブラリをインポートします。


In [1]:
import os

import datarobot as dr

os.environ['PULUMI_CONFIG_PASSPHRASE'] = 'default'

assert 'DATAROBOT_API_TOKEN' in os.environ, 'Please set the DATAROBOT_API_TOKEN environment variable'
assert 'DATAROBOT_ENDPOINT' in os.environ, 'Please set the DATAROBOT_ENDPOINT environment variable'

dr.Client()

## プロジェクトの設定

Pulumiスタックを作成または破棄する関数を設定します。


In [2]:
from pulumi import automation as auto


def stack_up(project_name: str, stack_name: str, program: callable) -> auto.Stack:
    # create (or select if one already exists) a stack that uses our inline program
    stack = auto.create_or_select_stack(
        stack_name=stack_name, project_name=project_name, program=program
    )

    stack.refresh(on_output=print)

    stack.up(on_output=print)
    return stack


def destroy_project(stack: auto.Stack):
    """Destroy pulumi project"""
    stack_name = stack.name
    stack.destroy(on_output=print)

    stack.workspace.remove_stack(stack_name)
    print(f"stack {stack_name} in project removed")

## 宣言型カスタムモデルデプロイの作成

このセルを使用して、カスタムモデルのデプロイを作成します。ソースコードをDataRobotに追加して、モデルを登録し、デプロイを初期化します。以下の`make_custom_deployment`関数は、これを宣言的に行う方法を示しています。すべてのアプリケーションテンプレートで、この関数のバリエーションを確認できます。



In [3]:
import pulumi_datarobot as datarobot
import pulumi


def make_custom_inference_deployment():
    """
    Deploy a trained model onto DataRobot's prediction environment.

    Upload source code to create a custom model version.
    Then create a registered model and deploy it to a prediction environment.
    """

    # ID for Python 3.9 Scikit learn drop in environment
    base_environment_id = "5e8c889607389fe0f466c72d"

    # ID for the default prediction server
    default_prediction_server_id = "5dd7fa2274a35f003102f60d"

    custom_model_name = "App Template Minis - Readmitted Custom Model"
    registered_model_name = "App Template Minis - Readmitted Registered Model"
    deployment_name = "App Template Minis - Readmitted Deployed Model"

    deployment_files = [
        ("./model_package/requirements.txt", "requirements.txt"),
        ("./model_package/custom.py", "custom.py"),
        ("./model_package/model.pkl", "model.pkl"),
    ]

    custom_model = datarobot.CustomModel(
        resource_name=custom_model_name,
        files=deployment_files,
        base_environment_id=base_environment_id,
        language="python",
        target_type="Binary",
        target_name="readmitted",
    )

    registered_model = datarobot.RegisteredModel(
        resource_name=registered_model_name,
        custom_model_version_id=custom_model.version_id,
    )

    deployment = datarobot.Deployment(
        resource_name=deployment_name,
        label=deployment_name,
        registered_model_version_id=registered_model.version_id,
        prediction_environment_id=default_prediction_server_id,
    )

    pulumi.export("custom_model_id", custom_model.id)
    pulumi.export("registered_model_id", registered_model.id)
    pulumi.export("deployment_id", deployment.id)

## Pulumiスタックの実行

これで、Pulumiスタックを実行できます。そうすることで、ダウンロードしたアセットから`model_package`ディレクトリ内のファイルが取り出されて、DataRobotにカスタムモデルとして配置され、そのモデルの登録と結果のデプロイが行われます。


In [ ]:
project_name = "AppTemplateMinis-CustomInferenceModels"
stack_name = "MarshallsCustomReadmissionsPredictor"

stack = stack_up(project_name, stack_name, program=make_custom_inference_deployment)

### 出力の操作

In [ ]:
from datarobot_predict.deployment import predict
import pandas as pd


df = pd.read_csv(
    "https://s3.amazonaws.com/datarobot_public_datasets/10k_diabetes.csv"
).tail(100)


deployment_id = stack.outputs().get("deployment_id").value
deployment = dr.Deployment.get(deployment_id)

predict(deployment, data_frame=df).dataframe.head(10).iloc[:, :2]

## 作業内容のクリア

カスタムモデルを維持する必要がない場合もあります。このセルを使用してスタックをシャットダウンし、DataRobotで作成されたアセットを削除します。


In [ ]:
destroy_project(stack)

## 添付資料

### スコアリングコードはどのように機能するか？

以下のコードは、DataRobotがカスタムモデルとの対話方法を認識できるようにアップロードする内容を示しています。最小限の変換でカスタム推論モデルをデプロイするため、モデルと対話するためのフックは2つしか定義されていませんが、[その他のフックも](https://docs.datarobot.com/ja/docs/mlops/deployment/custom-models/drum/custom-model-components.html)追加できます。この例のモデルは標準的なScikit-learn二値分類器であるため、フックを定義しなくても、DataRobotはモデルとの対話方法を判断できます。しかし、ほとんどのモデルアーティファクトには何らかのカスタムスコアリングロジックが必要であるため、この例には`custom.py`ファイルも含まれています。


In [ ]:
from IPython.display import Code

Code(filename="./model_package/custom.py", language="python")

### 何をデプロイしたか？

そもそもどうやって適合モデルを取得したのか気になる場合は、`fit_custom_model.py`でデータセットとモデル適合のコードを確認できます。この例では、10K diabetesデータセットを使ってRandom Forest二値分類器をトレーニングします。以下のコードは、モデルのトレーニングとpickleに使用されます。テンプレートの実行には重要ではありません。


In [ ]:
from IPython.display import Code

Code(filename="./fit_custom_model.py", language="python")